In [1]:
import sys
import os
import math

#sys.path.append('/usr/lib/python3.10/site-packages')
#sys.path.append('/home/adamhanna/.local/lib/python3.10/site-packages')
#sys.path.append('/usr/lib64/python3.10/site-packages')


#module_path = os.path.abspath(os.path.join('../../../..'))
#if module_path not in sys.path:
#    sys.path.append(module_path)

In [3]:
import math
import pandas as pd
import numpy as np

from bokeh.plotting import figure
from bokeh.io import output_notebook, show
from bokeh.models import ColumnDataSource
from pandas_datareader import data as pd_data_fetcher
from datetime import datetime, timedelta

from lib import calcMaxDDs, calcSharpe, calcCAGR, sortino_ratio, max_dd

output_notebook()

Loading BokehJS ...

# Backtests

In [6]:
loc = "./data/backtest/ethusd/"

In [7]:
dateparse = lambda dates: [pd.datetime.strptime(d, "%Y-%m-%d %H:%M:%S +0000 UTC") for d in dates]
data = pd.read_csv(loc+"/balances.csv", parse_dates=['created_at'], date_parser=dateparse)

/tmp/ipykernel_5648/2339701232.py:1: FutureWarning: The pandas.datetime class is deprecated and will be removed from pandas in a future version. Import from datetime module instead.
  dateparse = lambda dates: [pd.datetime.strptime(d, "%Y-%m-%d %H:%M:%S +0000 UTC") for d in dates]


In [8]:
data = data.iloc[1:]
data.head()

play_id          created_at  balance   nav  \
1  fdba7274-36bf-4a27-b123-8c36089e3173 2022-11-03 00:02:00     3.26  3.26   
2  fdba7274-36bf-4a27-b123-8c36089e3173 2022-11-03 00:03:00     3.26  3.26   
3  fdba7274-36bf-4a27-b123-8c36089e3173 2022-11-03 00:04:00     3.26  3.26   
4  fdba7274-36bf-4a27-b123-8c36089e3173 2022-11-03 00:05:00     3.26  3.26   
5  fdba7274-36bf-4a27-b123-8c36089e3173 2022-11-03 00:06:00     3.26  3.26   

   realizedPNL  unrealizedPNL  
1          0.0            0.0  
2          0.0            0.0  
3          0.0            0.0  
4          0.0            0.0  
5          0.0            0.0

In [9]:
data['percent_change'] = data['nav'].pct_change() + 1
daily = data.groupby([data['created_at'].dt.date])['percent_change'].prod()
daily = daily.to_frame()
daily = daily.iloc[1:]
daily.index = pd.to_datetime(daily.index)
daily['p2v return'] = daily['percent_change'] - 1
daily['p2v cumulative return'] = (daily['percent_change'].fillna(0)).cumprod()
daily.head()

percent_change  p2v return  p2v cumulative return
created_at                                                   
2022-11-04        1.000333    0.000333               1.000333
2022-11-05        1.000188    0.000188               1.000521
2022-11-06        0.999722   -0.000278               1.000243
2022-11-07        1.000614    0.000614               1.000857
2022-11-08        1.001830    0.001830               1.002689

In [12]:
p = figure(x_axis_type='datetime', width=900, height=600, title="cumulative return")
p.line(x = daily.index.values, y = daily['p2v cumulative return'].values, line_width=2, line_color="blue")
show(p)

In [13]:
positions = pd.read_csv(loc+"/positions.csv", parse_dates=['created_at'], date_parser=dateparse)
positions.head()

/tmp/ipykernel_5648/2339701232.py:1: FutureWarning: The pandas.datetime class is deprecated and will be removed from pandas in a future version. Import from datetime module instead.
  dateparse = lambda dates: [pd.datetime.strptime(d, "%Y-%m-%d %H:%M:%S +0000 UTC") for d in dates]


play_id          created_at instrument  size  \
0  fdba7274-36bf-4a27-b123-8c36089e3173 2021-08-11 00:16:00     ETHUSD   0.0   
1  fdba7274-36bf-4a27-b123-8c36089e3173 2021-08-11 00:16:00     ETHUSD   0.0   
2  fdba7274-36bf-4a27-b123-8c36089e3173 2021-08-11 00:16:00     ETHUSD   0.0   
3  fdba7274-36bf-4a27-b123-8c36089e3173 2021-08-11 00:16:00     ETHUSD   0.0   
4  fdba7274-36bf-4a27-b123-8c36089e3173 2021-08-11 00:16:00     ETHUSD   0.0   

   entry_price  price_err  
0          0.0        0.0  
1          0.0        0.0  
2          0.0        0.0  
3          0.0        0.0  
4          0.0        0.0

In [14]:
balances_and_position = pd.merge(left=positions, right=data, left_on='created_at', right_on='created_at')
balances_and_position.head()

play_id_x          created_at instrument   size  \
0  50b9967f-979a-4f78-b871-df524ebbc6f4 2022-11-03 00:16:00     ETHUSD -0.001   
1  50b9967f-979a-4f78-b871-df524ebbc6f4 2022-11-03 00:17:00     ETHUSD -0.001   
2  50b9967f-979a-4f78-b871-df524ebbc6f4 2022-11-03 00:18:00     ETHUSD -0.001   
3  50b9967f-979a-4f78-b871-df524ebbc6f4 2022-11-03 00:19:00     ETHUSD -0.002   
4  50b9967f-979a-4f78-b871-df524ebbc6f4 2022-11-03 00:20:00     ETHUSD -0.002   

   entry_price  price_err                             play_id_y  balance  \
0  1517.601518   0.000000  50b9967f-979a-4f78-b871-df524ebbc6f4     3.26   
1  1517.601518  -0.000295  50b9967f-979a-4f78-b871-df524ebbc6f4     3.26   
2  1517.601518  -0.000954  50b9967f-979a-4f78-b871-df524ebbc6f4     3.26   
3  1519.026492  -0.001873  50b9967f-979a-4f78-b871-df524ebbc6f4     3.26   
4  1519.026492  -0.001199  50b9967f-979a-4f78-b871-df524ebbc6f4     3.26   

        nav   realizedPNL  unrealizedPNL  percent_change  
0  3.260000 -2.000000e-07  -6.488924e-08             1.0  
1  3.260000 -2.000000e-07  -2.954332e-07             1.0  
2  3.259999 -2.000000e-07  -9.535449e-07             1.0  
3  3.259998 -4.000000e-07  -1.872482e-06             1.0  
4  3.259997 -4.000000e-07  -2.398011e-06             1.0

In [15]:
balances_and_position["leverage"] = balances_and_position["size"] / balances_and_position["nav"]
balances_and_position["abs_leverage"] = abs(balances_and_position["size"] / balances_and_position["nav"])
balances_and_position["leverage_pct_change"] = balances_and_position["leverage"][balances_and_position["size"] != 0].pct_change()
balances_and_position["abs_price_err"] = balances_and_position["price_err"].abs()
balances_and_position.tail()

play_id_x          created_at instrument  \
279280  7ffd46e2-13c0-4b0f-9497-458a2e6d4373 2023-05-15 23:56:00     ETHUSD   
279281  7ffd46e2-13c0-4b0f-9497-458a2e6d4373 2023-05-15 23:57:00     ETHUSD   
279282  7ffd46e2-13c0-4b0f-9497-458a2e6d4373 2023-05-15 23:58:00     ETHUSD   
279283  7ffd46e2-13c0-4b0f-9497-458a2e6d4373 2023-05-15 23:59:00     ETHUSD   
279284  7ffd46e2-13c0-4b0f-9497-458a2e6d4373 2023-05-16 00:00:00     ETHUSD   

            size  entry_price  price_err  \
279280  0.052806  1826.065269   0.004961   
279281  0.052806  1826.065269   0.004740   
279282  0.052806  1826.065269   0.004657   
279283  0.052806  1826.065269   0.004574   
279284  0.052806  1826.065269   0.004879   

                                   play_id_y   balance       nav  realizedPNL  \
279280  7ffd46e2-13c0-4b0f-9497-458a2e6d4373  3.474068  3.473806     0.214068   
279281  7ffd46e2-13c0-4b0f-9497-458a2e6d4373  3.474068  3.473817     0.214068   
279282  7ffd46e2-13c0-4b0f-9497-458a2e6d4373  3.474068  3.473822     0.214068   
279283  7ffd46e2-13c0-4b0f-9497-458a2e6d4373  3.474068  3.473826     0.214068   
279284  7ffd46e2-13c0-4b0f-9497-458a2e6d4373  3.474068  3.473810     0.214068   

        unrealizedPNL  percent_change  leverage  abs_leverage  \
279280      -0.000262        0.999993  0.015201      0.015201   
279281      -0.000250        1.000003  0.015201      0.015201   
279282      -0.000246        1.000001  0.015201      0.015201   
279283      -0.000242        1.000001  0.015201      0.015201   
279284      -0.000258        0.999995  0.015201      0.015201   

        leverage_pct_change  abs_price_err  
279280             0.000007       0.004961  
279281            -0.000003       0.004740  
279282            -0.000001       0.004657  
279283            -0.000001       0.004574  
279284             0.000005       0.004879

In [16]:
balances_and_position["abs_leverage"] = balances_and_position["leverage"].abs()
balances_and_position["abs_leverage"].mean()

0.03755297891747464

In [17]:
balances_and_position["abs_leverage"].max()

1.408901272013471

In [18]:
daily_balances_and_position = balances_and_position.groupby([data['created_at'].dt.date]).leverage.apply(lambda x: np.max(np.abs(x)))
daily_balances_and_position = daily_balances_and_position.to_frame()
daily_balances_and_position = daily_balances_and_position.iloc[1:]
daily_balances_and_position.index = pd.to_datetime(daily_balances_and_position.index)

daily_balances_and_position.tail()

leverage
created_at          
2023-05-11  0.027746
2023-05-12  0.066656
2023-05-13  0.044710
2023-05-14  0.022279
2023-05-15  0.038444

In [20]:
p = figure(x_axis_type='datetime', width=900, height=600, title="abs leverage")
p.line(x = daily_balances_and_position.index, y = daily_balances_and_position['leverage'].values, line_width=2, line_color="blue")
show(p)

In [23]:
daily_balances_and_position['leverage-p-change'] = daily_balances_and_position['leverage'].pct_change()
p = figure(x_axis_type='datetime', width=900, height=600, title="leverage-p-change")
p.line(x = daily_balances_and_position.index, y = daily_balances_and_position['leverage-p-change'].values, line_width=2, line_color="blue")
show(p)

In [24]:
daily_price_err = balances_and_position.groupby([data['created_at'].dt.date]).abs_price_err.apply(lambda x: np.max(np.abs(x)))
daily_price_err = daily_price_err.to_frame()
daily_price_err.index = pd.to_datetime(daily_price_err.index)

daily_price_err.tail()

abs_price_err
created_at               
2023-05-11       0.006591
2023-05-12       0.012507
2023-05-13       0.007463
2023-05-14       0.006329
2023-05-15       0.008711

In [26]:
p = figure(x_axis_type='datetime', width=900, height=600, title="abs price err")
p.line(x = daily_price_err.index, y = daily_price_err['abs_price_err'].values, line_width=2, line_color="blue")
show(p)

In [27]:
daily.tail()

percent_change  p2v return  p2v cumulative return
created_at                                                   
2023-05-12        1.000279    0.000279               1.064873
2023-05-13        1.000248    0.000248               1.065137
2023-05-14        1.000082    0.000082               1.065224
2023-05-15        1.000142    0.000142               1.065375
2023-05-16        0.999995   -0.000005               1.065370

In [28]:
calcMaxDDs(daily['p2v cumulative return'].values)

(0.01629378170061772, 11.0, 166)

In [29]:
calcSharpe(daily['p2v return'].fillna(0), 255.0, 0.03 / 365.0)

1.2958259957015263

In [30]:
calcSharpe(daily['p2v return'].fillna(0)[daily['p2v return'] != 0], 255.0, 0.00 / 365.0)

1.723632179792054

In [31]:
calcCAGR(daily['p2v cumulative return'].values[0], daily['p2v cumulative return'].values[-1], daily['p2v cumulative return'].index[0], daily['p2v cumulative return'].index[-1])

0.12651075186105643




# Live

In [32]:
from dateutil.parser import parse

In [33]:
loc = "./data/live/ethusd"

In [34]:
live_data = pd.read_csv(loc + "/balances.csv", parse_dates=['created_at'], date_parser=lambda x: parse(x))

In [35]:
live_data = live_data.iloc[1:]
data.head()

play_id          created_at  balance   nav  \
1  fdba7274-36bf-4a27-b123-8c36089e3173 2022-11-03 00:02:00     3.26  3.26   
2  fdba7274-36bf-4a27-b123-8c36089e3173 2022-11-03 00:03:00     3.26  3.26   
3  fdba7274-36bf-4a27-b123-8c36089e3173 2022-11-03 00:04:00     3.26  3.26   
4  fdba7274-36bf-4a27-b123-8c36089e3173 2022-11-03 00:05:00     3.26  3.26   
5  fdba7274-36bf-4a27-b123-8c36089e3173 2022-11-03 00:06:00     3.26  3.26   

   realizedPNL  unrealizedPNL  percent_change  
1          0.0            0.0             NaN  
2          0.0            0.0             1.0  
3          0.0            0.0             1.0  
4          0.0            0.0             1.0  
5          0.0            0.0             1.0

In [36]:
live_data['percent_change'] = live_data['net asset value'].pct_change() + 1
live_daily = live_data.groupby([live_data['created_at'].dt.date])['percent_change'].prod()
live_daily = live_daily.to_frame()
live_daily = live_daily.iloc[1:]
live_daily.index = pd.to_datetime(live_daily.index)
live_daily['p2v return'] = live_daily['percent_change'] - 1
live_daily['p2v cumulative return'] = (live_daily['percent_change'].fillna(0)).cumprod()
live_daily.tail()

percent_change  p2v return  p2v cumulative return
created_at                                                   
2023-05-17        1.000395    0.000395               1.060376
2023-05-18        1.000456    0.000456               1.060860
2023-05-19        1.000343    0.000343               1.061224
2023-05-20        1.000099    0.000099               1.061329
2023-05-21        1.000059    0.000059               1.061392

In [37]:
live_p = figure(x_axis_type='datetime', width=900, height=600, title="cumulative return")
live_p.line(x = live_daily.index.values, y = live_daily['p2v cumulative return'].values, line_width=2, line_color="blue")
show(live_p)

In [38]:
live_positions = pd.read_csv(loc + "/positions.csv", parse_dates=['created_at'], date_parser=lambda x: parse(x))
live_positions.head()

created_at instrument  size  entry_price
0 2022-11-03 00:00:40.426777+00:00    ETH-USD  0.07  1526.314286
1 2022-11-03 00:05:24.219035+00:00    ETH-USD  0.07  1526.314286
2 2022-11-03 00:10:24.676342+00:00    ETH-USD  0.07  1526.314286
3 2022-11-03 00:20:24.085970+00:00    ETH-USD  0.07  1526.314286
4 2022-11-03 00:30:40.434409+00:00    ETH-USD  0.07  1526.314286

In [39]:
live_prices = pd.read_csv(loc + "/prices.csv", parse_dates=['timestamp'], date_parser=lambda x: parse(x))
live_prices = live_prices.rename(columns={'timestamp': 'created_at'})
live_prices.head()

created_at exchange period instrument base quote        price
0 2022-11-03 00:00:00+00:00     DYDX    15M    ETH-USD  ETH   USD  1520.242353
1 2022-11-03 00:15:00+00:00     DYDX    15M    ETH-USD  ETH   USD  1516.516239
2 2022-11-03 00:30:00+00:00     DYDX    15M    ETH-USD  ETH   USD  1523.864976
3 2022-11-03 00:45:00+00:00     DYDX    15M    ETH-USD  ETH   USD  1527.813018
4 2022-11-03 01:00:00+00:00     DYDX    15M    ETH-USD  ETH   USD  1533.946676

In [40]:
live_balances_and_position = pd.merge_asof(left=live_positions, right=live_data, on='created_at')
live_balances_and_position.head()

created_at instrument  size  entry_price  currency  \
0 2022-11-03 00:00:40.426777+00:00    ETH-USD  0.07  1526.314286       NaN   
1 2022-11-03 00:05:24.219035+00:00    ETH-USD  0.07  1526.314286       NaN   
2 2022-11-03 00:10:24.676342+00:00    ETH-USD  0.07  1526.314286       NaN   
3 2022-11-03 00:20:24.085970+00:00    ETH-USD  0.07  1526.314286       NaN   
4 2022-11-03 00:30:40.434409+00:00    ETH-USD  0.07  1526.314286       NaN   

   net asset value  unrealized pnl  realized pnl      balance  percent_change  
0              NaN             NaN           NaN          NaN             NaN  
1      4993.238391             0.0          -1.0  4993.238391             NaN  
2      4993.238391             0.0          -1.0  4993.238391        1.000000  
3      4993.472998             0.0          -1.0  4993.472998        1.000047  
4      4993.871998             0.0          -1.0  4993.871998        1.000080

In [41]:
live_balances_and_position_and_prices = pd.merge_asof(left=live_balances_and_position, right=live_prices, on='created_at')
live_balances_and_position_and_prices['entry_price'] = np.where(live_balances_and_position_and_prices['entry_price'] == 0, live_balances_and_position_and_prices['price'], live_balances_and_position_and_prices['entry_price'])
live_balances_and_position_and_prices.head()

created_at instrument_x  size  entry_price  currency  \
0 2022-11-03 00:00:40.426777+00:00      ETH-USD  0.07  1526.314286       NaN   
1 2022-11-03 00:05:24.219035+00:00      ETH-USD  0.07  1526.314286       NaN   
2 2022-11-03 00:10:24.676342+00:00      ETH-USD  0.07  1526.314286       NaN   
3 2022-11-03 00:20:24.085970+00:00      ETH-USD  0.07  1526.314286       NaN   
4 2022-11-03 00:30:40.434409+00:00      ETH-USD  0.07  1526.314286       NaN   

   net asset value  unrealized pnl  realized pnl      balance  percent_change  \
0              NaN             NaN           NaN          NaN             NaN   
1      4993.238391             0.0          -1.0  4993.238391             NaN   
2      4993.238391             0.0          -1.0  4993.238391        1.000000   
3      4993.472998             0.0          -1.0  4993.472998        1.000047   
4      4993.871998             0.0          -1.0  4993.871998        1.000080   

  exchange period instrument_y base quote        price  
0     DYDX    15M      ETH-USD  ETH   USD  1520.242353  
1     DYDX    15M      ETH-USD  ETH   USD  1520.242353  
2     DYDX    15M      ETH-USD  ETH   USD  1520.242353  
3     DYDX    15M      ETH-USD  ETH   USD  1516.516239  
4     DYDX    15M      ETH-USD  ETH   USD  1523.864976

In [42]:
live_balances_and_position_and_prices["net asset value - BTC"] = live_balances_and_position_and_prices["net asset value"].fillna(0) / live_balances_and_position_and_prices["price"].fillna(1)
live_balances_and_position_and_prices["leverage"] = live_balances_and_position_and_prices["size"] / live_balances_and_position_and_prices["net asset value - BTC"].fillna(1)
live_balances_and_position_and_prices["abs_leverage"] = abs(live_balances_and_position_and_prices["leverage"])
live_balances_and_position_and_prices["leverage_pct_change"] = live_balances_and_position_and_prices["leverage"][live_balances_and_position_and_prices["size"] != 0].pct_change()
live_balances_and_position_and_prices["price_err"] = (live_balances_and_position_and_prices["entry_price"].fillna(0) - live_balances_and_position_and_prices["price"].fillna(0)) / live_balances_and_position_and_prices["price"].fillna(1)
live_balances_and_position_and_prices["abs_price_err"] = live_balances_and_position_and_prices["price_err"].abs()
live_balances_and_position_and_prices.head(100)

created_at instrument_x  size  entry_price  currency  \
0  2022-11-03 00:00:40.426777+00:00      ETH-USD  0.07  1526.314286       NaN   
1  2022-11-03 00:05:24.219035+00:00      ETH-USD  0.07  1526.314286       NaN   
2  2022-11-03 00:10:24.676342+00:00      ETH-USD  0.07  1526.314286       NaN   
3  2022-11-03 00:20:24.085970+00:00      ETH-USD  0.07  1526.314286       NaN   
4  2022-11-03 00:30:40.434409+00:00      ETH-USD  0.07  1526.314286       NaN   
..                              ...          ...   ...          ...       ...   
95 2022-11-03 12:20:23.942306+00:00      ETH-USD  0.00  1534.645342       NaN   
96 2022-11-03 12:30:40.362921+00:00      ETH-USD  0.01  1529.500000       NaN   
97 2022-11-03 12:35:23.642081+00:00      ETH-USD  0.01  1529.500000       NaN   
98 2022-11-03 12:40:24.565335+00:00      ETH-USD  0.01  1529.500000       NaN   
99 2022-11-03 12:45:40.647715+00:00      ETH-USD  0.01  1529.500000       NaN   

    net asset value  unrealized pnl  realized pnl      balance  \
0               NaN             NaN           NaN          NaN   
1       4993.238391             0.0          -1.0  4993.238391   
2       4993.238391             0.0          -1.0  4993.238391   
3       4993.472998             0.0          -1.0  4993.472998   
4       4993.871998             0.0          -1.0  4993.871998   
..              ...             ...           ...          ...   
95      4994.553201             0.0          -1.0  4994.553201   
96      4994.563640             0.0          -1.0  4994.563640   
97      4994.581296             0.0          -1.0  4994.581296   
98      4994.525592             0.0          -1.0  4994.525592   
99      4994.525592             0.0          -1.0  4994.525592   

    percent_change  ... instrument_y base quote        price  \
0              NaN  ...      ETH-USD  ETH   USD  1520.242353   
1              NaN  ...      ETH-USD  ETH   USD  1520.242353   
2         1.000000  ...      ETH-USD  ETH   USD  1520.242353   
3         1.000047  ...      ETH-USD  ETH   USD  1516.516239   
4         1.000080  ...      ETH-USD  ETH   USD  1523.864976   
..             ...  ...          ...  ...   ...          ...   
95        1.000000  ...      ETH-USD  ETH   USD  1534.645342   
96        1.000002  ...      ETH-USD  ETH   USD  1529.761931   
97        1.000004  ...      ETH-USD  ETH   USD  1529.761931   
98        0.999989  ...      ETH-USD  ETH   USD  1529.761931   
99        1.000000  ...      ETH-USD  ETH   USD  1529.818977   

   net asset value - BTC  leverage  abs_leverage  leverage_pct_change  \
0               0.000000       inf           inf                  NaN   
1               3.284502  0.021312      0.021312            -1.000000   
2               3.284502  0.021312      0.021312             0.000000   
3               3.292726  0.021259      0.021259            -0.002498   
4               3.277109  0.021360      0.021360             0.004766   
..                   ...       ...           ...                  ...   
95              3.254533  0.000000      0.000000                  NaN   
96              3.264929  0.003063      0.003063            -0.750087   
97              3.264940  0.003063      0.003063            -0.000004   
98              3.264904  0.003063      0.003063             0.000011   
99              3.264782  0.003063      0.003063             0.000037   

    price_err  abs_price_err  
0    0.003994       0.003994  
1    0.003994       0.003994  
2    0.003994       0.003994  
3    0.006461       0.006461  
4    0.001607       0.001607  
..        ...            ...  
95   0.000000       0.000000  
96  -0.000171       0.000171  
97  -0.000171       0.000171  
98  -0.000171       0.000171  
99  -0.000209       0.000209  

[100 rows x 22 columns]

In [43]:
live_balances_and_position_and_prices["abs_leverage"] = live_balances_and_position_and_prices["leverage"].abs()
live_balances_and_position_and_prices["abs_leverage"].mean()

inf

In [44]:
live_balances_and_position_and_prices["abs_leverage"].max()

inf

In [45]:
live_daily_balances_and_position = live_balances_and_position_and_prices.groupby([live_balances_and_position_and_prices['created_at'].dt.date]).leverage.apply(lambda x: np.max(np.abs(x)))
live_daily_balances_and_position = live_daily_balances_and_position.to_frame()
live_daily_balances_and_position = live_daily_balances_and_position.iloc[1:]
live_daily_balances_and_position.index = pd.to_datetime(live_daily_balances_and_position.index)

live_daily_balances_and_position.head()

leverage
created_at          
2022-11-04  0.043231
2022-11-05  0.020069
2022-11-06  0.037628
2022-11-07  0.047134
2022-11-08  0.142457

In [47]:
live_p = figure(x_axis_type='datetime', width=900, height=600, title="abs leverage")
live_p.line(x = live_daily_balances_and_position.index, y = live_daily_balances_and_position['leverage'].values, line_width=2, line_color="blue")
show(live_p)

In [48]:
live_daily_price_err = live_balances_and_position_and_prices.groupby([live_balances_and_position_and_prices['created_at'].dt.date]).abs_price_err.apply(lambda x: np.max(np.abs(x)))
live_daily_price_err = live_daily_price_err.to_frame()
live_daily_price_err.index = pd.to_datetime(live_daily_price_err.index)

live_daily_price_err.head()

abs_price_err
created_at               
2022-11-03       0.008596
2022-11-04       0.020707
2022-11-05       0.005219
2022-11-06       0.011639
2022-11-07       0.012006

In [50]:
live_p = figure(x_axis_type='datetime', width=900, height=600, title="abs price err")
live_p.line(x = live_daily_price_err.index, y = live_daily_price_err['abs_price_err'].values, line_width=2, line_color="blue")
show(live_p)

# Combined

## Daily

In [91]:
live_combined = pd.merge(left=live_daily_balances_and_position, right=daily_balances_and_position, left_on='created_at', right_on='created_at')
live_combined.head()

leverage_x  leverage_y  leverage-p-change
created_at                                           
2022-11-04    0.043231    0.060663                NaN
2022-11-05    0.020069    0.012196          -0.798957
2022-11-06    0.037628    0.032477           1.662970
2022-11-07    0.047134    0.040514           0.247466
2022-11-08    0.142457    0.066662           0.645402

In [92]:
live_combined_p = figure(x_axis_type='datetime', width=900, height=600, title="abs leverage")
live_combined_p.line(x = live_combined.index, y = live_combined['leverage_x'].values, line_width=2, line_color="blue", legend_label="live")
live_combined_p.line(x = live_combined.index, y = live_combined['leverage_y'].values, line_width=2, line_color="red", legend_label="backtest")
show(live_combined_p)

In [93]:
live_combined['leverage_x'].corr(live_combined['leverage_y'])

0.5260027938832905

In [94]:
live_combined = pd.merge(left=live_daily_price_err, right=daily_price_err, left_on='created_at', right_on='created_at')
live_combined.head()

abs_price_err_x  abs_price_err_y
created_at                                  
2022-11-03         0.008596         0.010357
2022-11-04         0.020707         0.022928
2022-11-05         0.005219         0.005177
2022-11-06         0.011639         0.015566
2022-11-07         0.012006         0.016900

In [95]:
live_combined_p = figure(x_axis_type='datetime', width=900, height=600, title="abs price err")
live_combined_p.line(x = live_combined.index, y = live_combined['abs_price_err_x'].values, line_width=2, line_color="blue", legend_label="live")
live_combined_p.line(x = live_combined.index, y = live_combined['abs_price_err_y'].values, line_width=2, line_color="red", legend_label="backtest")
show(live_combined_p)

In [96]:
live_combined['abs_price_err_x'].corr(live_combined['abs_price_err_y'])

0.7530901964028455

In [97]:
live_combined = pd.merge(left=live_daily, right=daily, left_on='created_at', right_on='created_at')
live_combined.tail()

percent_change_x  p2v return_x  p2v cumulative return_x  \
created_at                                                            
2023-05-12          1.000094      0.000094                 1.058240   
2023-05-13          1.000693      0.000693                 1.058973   
2023-05-14          1.000226      0.000226                 1.059213   
2023-05-15          1.000167      0.000167                 1.059389   
2023-05-16          1.000536      0.000536                 1.059957   

            percent_change_y  p2v return_y  p2v cumulative return_y  
created_at                                                           
2023-05-12          1.000279      0.000279                 1.064873  
2023-05-13          1.000248      0.000248                 1.065137  
2023-05-14          1.000082      0.000082                 1.065224  
2023-05-15          1.000142      0.000142                 1.065375  
2023-05-16          0.999995     -0.000005                 1.065370

In [100]:
live_combined_p = figure(x_axis_type='datetime', width=900, height=600, title="cumulative return")
live_combined_p.line(x = live_combined.index, y = live_combined['p2v cumulative return_x'].values, line_width=2, line_color="blue", legend_label="live")
live_combined_p.line(x = live_combined.index, y = live_combined['p2v cumulative return_y'].values, line_width=2, line_color="red", legend_label="backtest")
live_combined_p.legend.location = "top_left"
show(live_combined_p)

In [99]:
live_combined['p2v cumulative return_x'].corr(live_combined['p2v cumulative return_y'])

0.8857274589198372

## 5 MIN

In [61]:
balances_and_position['created_at'] = pd.to_datetime(balances_and_position['created_at'], utc=True)
live_combined = pd.merge_asof(left=live_balances_and_position_and_prices, right=balances_and_position, on='created_at')
live_combined.head()

created_at instrument_x  size_x  entry_price_x  \
0 2022-11-03 00:00:40.426777+00:00      ETH-USD    0.07    1526.314286   
1 2022-11-03 00:05:24.219035+00:00      ETH-USD    0.07    1526.314286   
2 2022-11-03 00:10:24.676342+00:00      ETH-USD    0.07    1526.314286   
3 2022-11-03 00:20:24.085970+00:00      ETH-USD    0.07    1526.314286   
4 2022-11-03 00:30:40.434409+00:00      ETH-USD    0.07    1526.314286   

   currency  net asset value  unrealized pnl  realized pnl    balance_x  \
0       NaN              NaN             NaN           NaN          NaN   
1       NaN      4993.238391             0.0          -1.0  4993.238391   
2       NaN      4993.238391             0.0          -1.0  4993.238391   
3       NaN      4993.472998             0.0          -1.0  4993.472998   
4       NaN      4993.871998             0.0          -1.0  4993.871998   

   percent_change_x  ...                             play_id_y balance_y  \
0               NaN  ...                                   NaN       NaN   
1               NaN  ...                                   NaN       NaN   
2          1.000000  ...                                   NaN       NaN   
3          1.000047  ...  50b9967f-979a-4f78-b871-df524ebbc6f4  3.260000   
4          1.000080  ...  50b9967f-979a-4f78-b871-df524ebbc6f4  3.259999   

        nav   realizedPNL unrealizedPNL  percent_change_y  leverage_y  \
0       NaN           NaN           NaN               NaN         NaN   
1       NaN           NaN           NaN               NaN         NaN   
2       NaN           NaN           NaN               NaN         NaN   
3  3.259997 -4.000000e-07     -0.000002          1.000000   -0.000613   
4  3.259988 -8.340166e-07     -0.000011          0.999999   -0.001279   

   abs_leverage_y  leverage_pct_change_y  abs_price_err_y  
0             NaN                    NaN              NaN  
1             NaN                    NaN              NaN  
2             NaN                    NaN              NaN  
3        0.000613           1.612054e-07         0.001199  
4        0.001279           5.435423e-07         0.002719  

[5 rows x 37 columns]

In [63]:
live_combined_p = figure(x_axis_type='datetime', width=900, height=600, title="cumulative return")
live_combined_p.line(x = live_combined['created_at'], y = (live_combined['net asset value'].pct_change() + 1).cumprod(), line_width=2, line_color="blue", legend_label="live")
live_combined_p.line(x = live_combined['created_at'], y = (live_combined['nav'].pct_change() + 1).cumprod(), line_width=2, line_color="red", legend_label="backtest")
live_combined_p.legend.location = "top_left"
show(live_combined_p)

In [64]:
(live_combined['net asset value'].pct_change() + 1).cumprod().corr((live_combined['nav'].pct_change() + 1).cumprod())

0.8907904165235383

In [65]:
((live_combined['net asset value'].pct_change() + 1).cumprod().values[-1]) ** (365 / (live_combined['created_at'].values[-1] - live_combined['created_at'].values[0]).astype('timedelta64[D]').astype(int)) - 1

0.11628711399385461

In [66]:
((live_combined['nav'].pct_change() + 1).cumprod().values[-1]) ** (365 / (live_combined['created_at'].values[-1] - live_combined['created_at'].values[0]).astype('timedelta64[D]').astype(int)) - 1

0.12357647159036378

In [67]:
calcSharpe(live_daily['p2v return'].fillna(0), 255.0, 0.03 / 365.0)

1.112462830090561

In [68]:
calcSharpe(daily['p2v return'].fillna(0), 255.0, 0.03 / 365.0)

1.2958259957015263

In [69]:
(365 / (live_combined['created_at'].values[-1] - live_combined['created_at'].values[0]).astype('timedelta64[D]').astype(int))

1.8341708542713568

In [71]:
live_combined_p = figure(x_axis_type='datetime', width=900, height=600, title="leverage")
live_combined_p.line(x = live_combined['created_at'], y = live_combined['leverage_x'], line_width=2, line_color="blue", legend_label="live")
live_combined_p.line(x = live_combined['created_at'], y = live_combined['leverage_y'], line_width=2, line_color="red", legend_label="backtest")
live_combined_p.legend.location = "top_left"
show(live_combined_p)

In [72]:
live_combined['leverage_x'].corr(live_combined['leverage_y'])

0.46080847993949237

In [78]:
live_combined_p = figure(x_axis_type='datetime', width=900, height=600, title="abs leverage")
live_combined_p.line(x = live_combined['created_at'], y = live_combined['abs_leverage_x'], line_width=2, line_color="blue")
live_combined_p.line(x = live_combined['created_at'], y = live_combined['abs_leverage_y'], line_width=2, line_color="red")
show(live_combined_p)

In [79]:
live_combined['abs_leverage_x'].corr(live_combined['abs_leverage_y'])

0.4003746576123513

In [80]:
live_combined.replace([np.inf, -np.inf], np.nan)['abs_leverage_x'].mean()

0.05317907430964629

In [81]:
live_combined['abs_leverage_y'].mean()

0.03693708545149831

In [83]:
live_combined_p = figure(x_axis_type='datetime', width=900, height=600, title="price err")
live_combined_p.line(x = live_combined['created_at'], y = live_combined['price_err_x'], line_width=2, line_color="blue", legend_label="live")
live_combined_p.line(x = live_combined['created_at'], y = live_combined['price_err_y'], line_width=2, line_color="red", legend_label="backtest")
live_combined_p.legend.location = "top_right"
show(live_combined_p)

In [84]:
live_combined['price_err_x'].corr(live_combined['price_err_y'])

0.6506904563628112

In [86]:
live_combined_p = figure(x_axis_type='datetime', width=900, height=600, title="abs_price_err")
live_combined_p.line(x = live_combined['created_at'], y = live_combined['abs_price_err_x'], line_width=2, line_color="blue")
live_combined_p.line(x = live_combined['created_at'], y = live_combined['abs_price_err_y'], line_width=2, line_color="red")
show(live_combined_p)

In [87]:
live_combined['abs_price_err_x'].corr(live_combined['abs_price_err_y'])

0.6397578449151399

In [88]:
live_combined['abs_price_err_x'].mean()

0.004486486042388782

In [89]:
 live_combined['abs_price_err_y'].mean()

0.002912075621831982